# Visualize Traffic Accidents in UK by Road Types with Bokeh Datashader

by [Johnny Chan](https://github.com/Atlas7) | [GitHub Repo](https://github.com/Atlas7/visualize-traffic-accidents-in-uk) | [MIT Licence](https://github.com/Atlas7/visualize-traffic-accidents-in-uk/blob/master/LICENSE)

![datashader-uk-traffic-banner.jpg](../assets/images/datashader-uk-traffic-banner-2.jpg)

Towards the end of our introductory notebook [Visualize Traffic Accidents in UK with Datashader](https://nbviewer.jupyter.org/github/Atlas7/visualize-traffic-accidents-in-uk/blob/master/notebooks/Visualize-Traffic-Accidents-in-UK-with-Datashader.ipynb#) we successfully plotted a visualization of traffic accidents in UK categorized by `Road_Type`. From the plot we were able to visualize traffic accidents occuring on Single/Dual Carriageway, Roundabouts, and so on. One to-do list item from the notebook was to encapsulate away some of the codes and handy utility functions into a library.

On this, I've created a Python module [`utils`](`./scripts/utils.py`), which is stored under the [`./scripts`](./scripts) directory. In thie notebook I will show you how to call these utilities, so our codes become shorter and more compact. Notice now we now have this line in our Import section:

```
from scripts.utils import add_webm_xys, get_plot_params, base_plot
```

Feel free to take a look at [`./scripts/utils.py`](./scripts/utils.py) yourself. It's pretty much derived from the introductory notebook, wrapped inside functions.

At the end of the notebook we will have these two interactive Bokeh Datashader plots: a standalone datashader plot, and the same plot with a map overlay.

---

See [README](https://github.com/Atlas7/visualize-traffic-accidents-in-uk/blob/master/README.md) for instructions on running this notebook on your machine locally.

---

## Setup Notebook

In [1]:
%matplotlib inline
%load_ext autoreload
%autoreload 2

## Import Libraries

In [2]:
import pandas as pd
import datashader as ds
from bokeh.plotting import figure, output_notebook, show
from bokeh.tile_providers import STAMEN_TERRAIN
from datashader.colors import Hot
from datashader import transfer_functions as tf
from datashader.bokeh_ext import InteractiveImage
from scripts.utils import add_webm_xys, get_plot_params, base_plot

## Enable Inline Bokeh Chart

In [3]:
output_notebook()

Loading BokehJS ...

## Prepare Data

Just to keep things simple, let's just use the 2005-2007 dataset for now.

In [4]:
%%time
df = pd.read_csv('../input/accidents_2005_to_2007.csv', usecols=['Longitude','Latitude', 'Road_Type'])

CPU times: user 981 ms, sys: 62.2 ms, total: 1.04 s
Wall time: 1.04 s


In [5]:
# ensure all category variables has the `category` type so datashader can do aggregation accordingly
df['Road_Type'] = df['Road_Type'].astype('category')

In [6]:
# add the Web Mercator `webm_x` and `web_y` columns from our Logitude and Latitude values
df = add_webm_xys(df)

In [7]:
# take a peek
df.dtypes

Longitude     float64
Latitude      float64
Road_Type    category
webm_x        float64
webm_y        float64
dtype: object

In [8]:
# take a peek
df.tail()

Longitude   Latitude           Road_Type         webm_x        webm_y
570006  -3.210294  54.985289  Single carriageway -357368.293377  7.359012e+06
570007  -3.193693  54.984105  Single carriageway -355520.278510  7.358782e+06
570008  -2.992068  55.166369  Single carriageway -333075.486179  7.394222e+06
570009  -3.058338  54.995154  Single carriageway -340452.628834  7.360926e+06
570010  -3.348857  55.104618  Single carriageway -372793.055979  7.382197e+06

## Define Bounding Boxes

In [9]:
# in lng/lats, manually obatained from Open Street Map
# https://www.openstreetmap.org/export
# feel free to add some of your own!
bboxes = {
  "gb": ((-15.381, 7.251), (48.749, 61.502)),
  "gb_mainland": ( (-12.129, 5.120), (49.710, 58.745)),
  "gb_long": ((-8.745, 2.241), (48.749, 61.502)),
  "gb_wide": ((-21.709, 15.293), (48.749, 61.502)),
  "london": ((-0.643, 0.434), (51.200, 51.761)),
  "london_2": ((-0.1696, 0.0130), (51.4546, 51.5519)),
  "london_3": ((-0.1330, -0.0235), (51.4741, 51.5322)),  
  "manchester": ((-3.049, -1.505), (52.975, 53.865))
}

## Define Color Key for Road Types

In [10]:
# What Road_Type values do we have?
df.groupby(['Road_Type']).size()

Road_Type
Dual carriageway       87274
One way street         12434
Roundabout             36637
Single carriageway    423414
Slip road               5936
Unknown                 4316
dtype: int64

In [11]:
# Build a color_key that maps each Road_Type values with a Bokeh color palette
# https://bokeh.pydata.org/en/latest/docs/reference/colors.html
color_key = {
  'Dual carriageway':'red',
  'One way street':'orange',
  'Roundabout':'yellow',
  'Single carriageway':'green',
  'Slip road':'blue',
  'Unknown':'purple'
}

## Define Callback Function

We use `ds.count_cat` to perform aggregation traffic accident counts by `Road_Type`. All callback functions will be somewhat similar to this. When we perform separate analysis in other future notebooks, do feel free just copy this callback function, and change it as required.

In [12]:
def agg_by_road_type(x_range, y_range, w, h):
  cvs = ds.Canvas(x_range=x_range, y_range=y_range, plot_width=w, plot_height=h)
  agg = cvs.points(df, 'webm_x', 'webm_y',  ds.count_cat('Road_Type'))
  img = tf.shade(agg, cmap=Hot, color_key=color_key, how='eq_hist')
  return tf.dynspread(img, threshold=0.5, max_px=4)

## Interactive Image 1 - Datashader Visualization

In [13]:
p = base_plot(*get_plot_params(bboxes["gb"], plot_width=800), background_fill_color="black")
InteractiveImage(p, agg_by_road_type)

## Interactive Image 2 - Map Overlay

In [14]:
p = base_plot(*get_plot_params(bboxes["gb"], plot_width=800), background_fill_color="black")
p.add_tile(STAMEN_TERRAIN)  # overlay our plot on a STAMEN_TWERRAIN map
InteractiveImage(p, agg_by_road_type)

## Conclusion

We have packed away some of the useful utiliy functions learnt from our introductory notebook [Visualize Traffic Accidents in UK with Datashader](https://nbviewer.jupyter.org/github/Atlas7/visualize-traffic-accidents-in-uk/blob/master/notebooks/Visualize-Traffic-Accidents-in-UK-with-Datashader.ipynb#) and used them in this notebook, making the codes shorter and more concise. We have written much shorter codes in to building of the Bokeh Datashader interactive map, showing the visualization of traffic accidents in the UK by Road Type.